In [1]:
import datetime
import math
import time
import itertools
from contextlib import closing
from collections import OrderedDict
import json
import numpy as np
import pandas as pd
import MySQLdb
import pymssql
from sqlalchemy import create_engine
import dfutils

In [2]:
pd.set_option('display.max_rows', 1500)
pd.set_option('display.max_columns', 500)

In [3]:
def optimized_execute(query, commit=False):
    '''
    Executes the search query in Northpoint
    '''
    
    with closing(pymssql.connect(host='10.16.1.16', user='readonly_user', password='readonly_user',
                                 database='PnLAppDb')) as np_pnl_conn:
        with closing(np_pnl_conn.cursor()) as np_pnl_cursor:
            np_pnl_cursor.execute(query)
            if commit:
                np_pnl_conn.commit()
                return

            fetched_res = np_pnl_cursor.fetchall()  # fetch (and discard) remaining rows\
            return fetched_res

In [4]:
def get_position_calculated_values_history_max_date():  # done
    query = "SELECT MAX(PCVH.TradeDate) FROM [PnLAppDb].[dbo].[PositionCalculatedValuesHistory] AS PCVH "
    results = optimized_execute(query)
    if len(results) == 0:
        return None

    return results[0][0]

In [5]:
def get_position_calculated_values_history(start_date_yyyy_mm_dd=None, end_date_yyyy_mm_dd=None,
                                           limit_to_tradegroups=[], is_tg_names_in_tradar_format=False,
                                           fund_code=None, NP_qty_rollup=True):
    if start_date_yyyy_mm_dd is None or end_date_yyyy_mm_dd is None:
        start_date_yyyy_mm_dd = '2019-03-01'
        end_date_yyyy_mm_dd = get_position_calculated_values_history_max_date()
    tg_filter_clause = ""
    if len([tg for tg in limit_to_tradegroups if tg is not None]) > 0:
        tg_filter_clause = " AND PCVH.TradeGroup IN (" + ",".join([("'" + tg + "'") 
                                                                   for tg in limit_to_tradegroups 
                                                                   if tg is not None]) + ") "
        if is_tg_names_in_tradar_format: 
            tg_filter_clause = tg_filter_clause.replace('PCVH.TradeGroup', 'SUBSTRING(PCVH.TradeGroup,0,21)')
            
    fund_code_filtuer_clause = " " if fund_code is None else " AND PCVH.FundCode = '" + fund_code + "' "
    # region query
    # New Fund by added bv Kshitij "WATER ISLAND MERGER ARBITRAGE INSTITUTIONAL":"MACO"
    query = "SELECT " \
            "PCVH.TradeDate, " \
            "ISNULL(PCVH.FundCode, " \
            "CASE F.FundName " \
            "WHEN 'Columbia' THEN 'CAM' " \
            "WHEN 'Litman Gregory' THEN 'LG' " \
            "WHEN 'The Arbitrage Credit Opportunities Fund' THEN 'TACO' " \
            "WHEN 'The Arbitrage Event-Driven Fund' THEN 'AED' " \
            "WHEN 'The Arbitrage Fund' THEN 'ARB' " \
            "WHEN 'TransAmerica' THEN 'TAF' " \
            "WHEN 'WIC Arbitrage Partners' THEN 'WIC' " \
            "WHEN 'The Arbitrage Tactical Equity Fund' THEN 'TAQ' " \
            "WHEN 'Water Island Event-Driven Fund' THEN 'WED' " \
            "WHEN 'Water Island Capital Lev Arb Fund' THEN 'WED' " \
            "WHEN 'WATER ISLAND MERGER ARBITRAGE INSTITUTIONAL' THEN 'MACO' " \
            "WHEN 'Morningstar Alternatives Fund' THEN 'MALT' " \
            "END " \
            ") AS FundCode, " \
            "SPT_TRDGRP.SecName AS TradeGroup, " \
            "SPT_TRDGRP.SecName AS TradeGroup_Tradar_Name, " \
            "PCVH.[Marketing GROUP] AS Sleeve,   " \
            "ISNULL(PCVH.[Bucket],'NA') AS Bucket, " \
            "PCVH.TradeGroupId, " \
            "SPT.StandardTicker As Ticker, " \
            "SPT.BloombergGlobalId, " \
            "SPT.BloombergGID, " \
            "ISNULL(SPT.BloombergGlobalId,SPT.BloombergGID) AS BBGID, " \
            "SPT.SecType, " \
            "ISNULL(SPT.MarketCapCategory, 'N/A') AS MarketCapCategory, " \
            "PCVH.SecurityID, " \
            "PCVH.DealTermsCash, " \
            "PCVH.DealTermsStock, " \
            "PCVH.DealValue, " \
            "PCVH.DealClosingDate, " \
            "CASE " \
            "WHEN SPT.SecType = 'FxFwd' THEN 0.0 " \
            "WHEN SPT.SecType <> 'FxFwd' AND PCVH.[Marketing GROUP] = 'Equity Special Situations'  THEN 1.0 " \
            "WHEN SPT.SecType <> 'FxFwd' AND PCVH.[Marketing GROUP] = 'Opportunistic'  THEN 1.0 " \
            "WHEN SPT.SecType <> 'FxFwd' AND PCVH.[Marketing GROUP] = 'Merger Arbitrage'  THEN " \
            "CASE WHEN ISNULL(PCVH.AlphaHedge,'NA') IN ('Alpha','Alpha Hedge') THEN " \
            "CASE PCVH.DealValue WHEN 0 THEN 0.0 ELSE PCVH.DealTermsStock/PCVH.DealValue END " \
            "ELSE 1.0 END " \
            "WHEN SPT.SecType <> 'FxFwd' AND PCVH.[Marketing GROUP] = 'Credit Opportunities'  THEN " \
            "CASE WHEN SPT.SecType IN ('EQ','ExchOpt') THEN 1.0 ELSE 0.0 END " \
            "ELSE NULL END " \
            "AS [Equity Risk Factor], " \
            "PCVH.DV_01, " \
            "PCVH.CR_01, " \
            "PCVH.Adj_CR_01, " \
            "ISNULL(SPT.UltimateCountry,'N/A') AS UltimateCountry, " \
            "ISNULL(PCVH.AlphaHedge,'NA') AS AlphaHedge, " \
            "SUM(PCVH.ExposureLong_USD) AS Exposure_Long, " \
            "SUM(PCVH.ExposureShort_USD) AS Exposure_Short, " \
            "SUM(PCVH.ExposureLong_USD+PCVH.ExposureShort_USD) AS Exposure_Net, " \
            "CASE WHEN NAV.NAV = 0 THEN NULL " \
            "ELSE 100.0*(SUM(PCVH.ExposureLong_USD+PCVH.ExposureShort_USD)/NAV.NAV) END " \
            "AS [Exposure_Net(%)], " \
            "SUM(PCVH.MktValLong_USD+PCVH.MktValShort_USD) AS NetMktVal, " \
            "CASE WHEN ISNULL(PCVH.AlphaHedge,'NA') IN ('Alpha','Alpha Hedge') " \
            "THEN ABS(SUM(PCVH.MktValLong_USD+PCVH.MktValShort_USD)) ELSE NULL END AS Capital, " \
            "CASE WHEN ISNULL(PCVH.AlphaHedge,'NA') IN ('Alpha','Alpha Hedge') " \
            "THEN 100.0*(ABS(SUM(PCVH.MktValLong_USD+PCVH.MktValShort_USD))/NAV.NAV) ELSE NULL " \
            "END AS [Capital % of NAV], " \
            "100.0*SUM(PCVH.Base_Case_NAV_Impact) AS BaseCaseNavImpact, " \
            "100.0*SUM(PCVH.Outlier_NAV_Impact) AS OutlierNavImpact, " \
            "SUM(PCVH.Qty) AS QTY, " \
            "ISNULL(PCVH.TradeGroupLongShortFlag,'NA') AS LongShort, " \
            "ISNULL(SPT.GICSSectorName,'NA') AS Sector, " \
            "ISNULL(SPT.GICSIndustryName,'NA') AS Industry, " \
            "ISNULL(PCVH.TradeGroupCatalystRating, 'NA') AS CatalystRating, " \
            "CASE ISNULL(PCVH.TradeGroupCatalystRating, 'NA') " \
            "   WHEN 'NA' THEN 'N/A' " \
            "   WHEN 0 THEN 'No Catalyst' " \
            "   WHEN 1 THEN 'Soft' " \
            "   WHEN 2 THEN 'Binary' " \
            "   WHEN 3 THEN 'Hard' " \
            "   ELSE 'Unknown' END AS CatalystName, " \
            "NAV.NAV " \
            "FROM [PnLAppDb].[dbo].[PositionCalculatedValuesHistory] AS PCVH " \
            "INNER JOIN PnLAppDb.dbo.Funds AS F ON PCVH.Portfolio = F.FundID " \
            "INNER JOIN SecurityMaster.dbo.SecurityPivotTable AS SPT ON PCVH.SecurityID = SPT.ID " \
            "INNER JOIN SecurityMaster.dbo.SecurityPivotTable AS SPT_TRDGRP ON PCVH.TradeGroupId = SPT_TRDGRP.ID " \
            "LEFT OUTER JOIN PnLAppDb.pnl.DailyNAV AS NAV ON PCVH.Portfolio = NAV.FundId " \
            "AND PCVH.TradeDate = NAV.[DATE] " \
            "WHERE  TradeDate >= '" + start_date_yyyy_mm_dd + "' AND TradeDate <= '" + end_date_yyyy_mm_dd + "' " \
            + tg_filter_clause + \
            fund_code_filtuer_clause + \
            " AND PCVH.Qty <> 0 " \
            "GROUP BY " \
            "F.FundName, PCVH.FundCode,PCVH.TradeDate, PCVH.[Marketing GROUP], SPT_TRDGRP.SecName, " \
            "PCVH.TradeGroupId, SPT.StandardTicker, SPT.BloombergGlobalId, SPT.BloombergGID, " \
            "SPT.SecType, ISNULL(SPT.MarketCapCategory, 'N/A'), " \
            "PCVH.SecurityId, SPT.UltimateCountry, " \
            "ISNULL(PCVH.AlphaHedge,'NA'),PCVH.TradeGroupLongShortFlag, ISNULL(SPT.GICSSectorName,'NA'), " \
            "ISNULL(SPT.GICSIndustryName,'NA'), ISNULL(PCVH.TradeGroupCatalystRating, 'NA'), " \
            "ISNULL(PCVH.[Bucket],'NA'), PCVH.DealTermsCash, PCVH.DealTermsStock, " \
            "PCVH.DealValue, PCVH.DealClosingDate, " \
            "PCVH.DV_01, PCVH.CR_01, PCVH.Adj_CR_01, NAV.NAV, PCVH.Analyst " \
            "ORDER BY PCVH.TradeDate "
    # endregion
    results = optimized_execute(query)
    df = pd.DataFrame(results, columns=["Date", "FundCode", "TradeGroup", "TradeGroup_Tradar_Name", "Sleeve",
                                        "Bucket", "TradeGroupId", "Ticker", "BloombergGlobalId", "BloombergGID", "BBGID", "SecType", "MarketCapCategory",
                                        "SecurityId", "DealTermsCash", "DealTermsStock", "DealValue", 
                                        "DealClosingDate", "Equity_Risk_Factor", "DV01", "CR01", "Adj_CR01",
                                        "UltimateCountry", "AlphaHedge", "Exposure_Long", "Exposure_Short",
                                        "Exposure_Net", "Exposure_Net(%)", "NetMktVal", "Capital($)", 
                                        "Capital(%)", "BaseCaseNavImpact", "OutlierNavImpact", "Qty", 
                                        "LongShort", "Sector", "Industry", "CatalystRating", "CatalystName", "Fund_NAV"])

    float_cols = ['NetMktVal', 'Capital($)', 'Capital(%)', 'Exposure_Net', 'Exposure_Net(%)', 'BaseCaseNavImpact']
    df[float_cols] = df[float_cols].astype(float)
    df['Equity_Risk_Exp'] = df['Equity_Risk_Factor'].astype(float)*df['Exposure_Net'].astype(float)
    df[['DV01', 'CR01', 'Adj_CR01']] = df[['DV01', 'CR01', 'Adj_CR01']].fillna(0).astype(float)
    df["Date"] = df["Date"].apply(lambda x: pd.to_datetime(x))
    df["DealClosingDate"] = df["DealClosingDate"].apply(lambda x: pd.to_datetime(x))

    as_of_dt = datetime.datetime.strptime(end_date_yyyy_mm_dd, '%Y-%m-%d')

    def duration_calc(days):
        if days <= 90:
            return '0M-3M'
        if days <= 180:
            return '3M-6M'
        if days <= 365:
            return '6M-12M'
        return 'Yr+'

    df["DealDuration"] = df["DealClosingDate"].apply(lambda x: None if pd.isnull(x) else
                                                     duration_calc((as_of_dt - pd.to_datetime(x)).days))

    # region ADJUSTING FOR POSTED TRADES AFTER TRADE DATE - AFFECTING QTY ONLY
    # adjust for end_date_yyyy_mm_dd - take trades with tradedate = end_date_yyyy_mm_dd and posted_date
    #AFTER end_date_yyyy_mm_dd
    # adjust the Qty into the pcvh_df
    if NP_qty_rollup:
        qty_adjust_query = "SELECT " \
                            "A.TradeDate AS [DATE], " \
                            "CASE A.Fund " \
                            "WHEN 'Columbia' THEN 'CAM' " \
                            "WHEN 'Litman Gregory' THEN 'LG' " \
                            "WHEN 'The Arbitrage Credit Opportunities Fund' THEN 'TACO' " \
                            "WHEN 'The Arbitrage Event-Driven Fund' THEN 'AED' " \
                            "WHEN 'The Arbitrage Fund' THEN 'ARB' " \
                            "WHEN 'TransAmerica' THEN 'TAF' " \
                            "WHEN 'WIC Arbitrage Partners' THEN 'WIC' " \
                            "WHEN 'The Arbitrage Tactical Equity Fund' THEN 'TAQ' " \
                            "WHEN 'Water Island Event-Driven Fund' THEN 'WED' " \
                            "WHEN 'Water Island Capital Lev Arb Fund' THEN 'LEV' " \
                            "WHEN 'WATER ISLAND MERGER ARBITRAGE INSTITUTIONAL COMMINGLED MASTER FUND LP' THEN 'MACO' " \
                            "WHEN 'Morningstar Alternatives Fund' THEN 'MALT' " \
                            "END AS FundCode, " \
                            "A.TradeGroupId, " \
                            "A.SecurityId, " \
                            "SUM((CASE SPT.SecType WHEN 'ExchOpt' THEN 100.0 ELSE 1.0 END)*A.Shares) AS Qty " \
                            "FROM " \
                            "[PnLAppDb].[dbo].[vTradesFlatView] AS A " \
                            "INNER JOIN SecurityMaster.dbo.SecurityPivotTable AS SPT ON A.SecurityId = SPT.ID " \
                            "WHERE PostedDate >= DATEADD(DAY,1,TradeDate) AND TradeDate >= '" \
                            + start_date_yyyy_mm_dd + "' " \
                            "GROUP BY A.TradeDate, A.SecurityId, A.Ticker, A.Fund, A.TradeGroupId, SPT.SecType "
        results = optimized_execute(qty_adjust_query)
        qty_adjust_df = pd.DataFrame(results, columns=['Date', 'FundCode', 'TradeGroupId', 'SecurityId', 'Qty_adj'])
        qty_adjust_df[['TradeGroupId', 'SecurityId', 'Qty_adj']] = qty_adjust_df[['TradeGroupId',
                                                                                  'SecurityId', 'Qty_adj']].astype(float)
        qty_adjust_df['Date'] = qty_adjust_df['Date'].apply(lambda x: pd.to_datetime(x))

        df[['TradeGroupId', 'SecurityId', 'Qty']] = df[['TradeGroupId', 'SecurityId', 'Qty']].astype(float)
        df = pd.merge(df, qty_adjust_df, how='left', on=['Date', 'FundCode', 'TradeGroupId', 'SecurityId'])
        df['Qty'] = df['Qty'] + df['Qty_adj'].fillna(0)
        del df['Qty_adj']
    # endregion
    print('PCVH retrieval completed....')
    return df

In [6]:
PCVH_new = get_position_calculated_values_history(start_date_yyyy_mm_dd='2019-05-16', end_date_yyyy_mm_dd='2019-05-16')

PCVH retrieval completed....


In [7]:
df_flat_file_new = pd.read_csv('C:/Users/aduprey/Desktop/COMBINED_5_16.csv')

In [15]:
def generate_files(np_data, eze_data):

    #np_data['Date'] = np_data['Date'].apply(lambda x: x.strftime('%Y-%m-%d'))
    np_data['TradeGroup'] = np_data['TradeGroup'].apply(lambda x: x.upper())
    np_data['Ticker'] = np_data['Ticker'].apply(lambda x: x.upper())
    np_data['Industry'] = np_data['Industry'].apply(lambda x: x.upper())
    np_data['Sector'] = np_data['Sector'].apply(lambda x: x.upper())
    np_data = np_data[np_data.SecType != 'FxFwd']

    eze_data['TradeGroup'] = eze_data['TradeGroup'].apply(lambda x: x.upper()) 
    eze_data = eze_data[eze_data.SecType != 'FXFWD']
    eze_data = eze_data[eze_data.FundCode != 'ETF1']
    eze_data = eze_data[eze_data.FundCode != 'ETF2']
    eze_data = eze_data[eze_data.FundCode != 'INDEX1']
    eze_data = eze_data[eze_data.FundCode != 'INDEX2']
    eze_data = eze_data[eze_data.FundCode != 'ETF3']
    eze_data = eze_data[eze_data.FundCode != 'INDEX3']

    np_bonds = np_data[(np_data.SecType == "B")|(np_data.SecType == 'CVB')].copy()
    eze_bonds = eze_data[(eze_data.SecType == "B")|(eze_data.SecType == 'CVB')].copy()

    bonds_df = pd.merge(np_bonds, eze_bonds, how='outer', on=['Date', 'FundCode', 'TradeGroup', 'BloombergGID'])

    np_equity_options = np_data[(np_data.SecType != 'B')&(np_data.SecType != 'CVB')].copy()
    eze_equity_options = eze_data[(eze_data.SecType != 'B')&(eze_data.SecType != 'CVB')].copy()

    equity_options_df = pd.merge(np_equity_options, eze_equity_options, how='outer', on=['Date', 'FundCode', 'TradeGroup', 'Ticker'])
    qty_bonds_df = bonds_df[['Date', 'FundCode', 'BloombergGID', 'TradeGroup', 'Ticker_x', 'Ticker_y', 'Qty_x', 'Qty_y']]
    qty_bonds_df = qty_bonds_df.rename(columns={'Ticker_x':'Ticker'})
    qty_eq_op_df = equity_options_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'Qty_x', 'Qty_y']]
    qty_df = pd.concat([qty_bonds_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'Qty_x', 'Qty_y']], qty_eq_op_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'Qty_x', 'Qty_y']]])
    qty_df = qty_df.sort_values(by=['TradeGroup', 'FundCode']).rename(columns={'Qty_x':'Qty_NP', 'Qty_y':'Qty_Eze'})
    qty_df['T/F'] = abs((qty_df['Qty_NP']-qty_df['Qty_Eze'])/(qty_df['Qty_Eze'])) <= 0.005
    qty_df = qty_df[qty_df['T/F'] == False].sort_values(by=['TradeGroup', 'FundCode'])
    qty_df.to_excel('C:/Users/aduprey/Desktop/qty_05_15.xlsx')

    exp_bonds_df = bonds_df[['Date', 'FundCode', 'BloombergGID', 'TradeGroup', 'Ticker_x', 'Ticker_y', 'Exposure_Net_x', 'Exposure_Net_y']]
    exp_bonds_df = exp_bonds_df.rename(columns={'Ticker_x':'Ticker'})
    exp_eq_op_df = equity_options_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'Exposure_Net_x', 'Exposure_Net_y']]
    exp_df = pd.concat([exp_bonds_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'Exposure_Net_x', 'Exposure_Net_y']], exp_eq_op_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'Exposure_Net_x', 'Exposure_Net_y']]])
    exp_df = exp_df.sort_values(by=['TradeGroup', 'FundCode']).rename(columns={'Exposure_Net_x':'Exposure_Net_NP', 'Exposure_Net_y':'Exposure_Net_Eze'})
    exp_df['T/F'] = abs((exp_df['Exposure_Net_NP']-exp_df['Exposure_Net_Eze'])/(exp_df['Exposure_Net_Eze'])) <= 0.03
    exp_df = exp_df[exp_df['T/F'] == False].sort_values(by=['TradeGroup', 'FundCode'])
    exp_df.to_excel('C:/Users/aduprey/Desktop/exp_net_05_15.xlsx')

    cap_bonds_df = bonds_df[['Date', 'FundCode', 'BloombergGID', 'TradeGroup', 'Ticker_x', 'Ticker_y', 'Capital($)_x', 'Capital($)_y']]
    cap_bonds_df = cap_bonds_df.rename(columns={'Ticker_x':'Ticker'})
    cap_eq_op_df = equity_options_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'Capital($)_x', 'Capital($)_y']]
    cap_df = pd.concat([cap_bonds_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'Capital($)_x', 'Capital($)_y']], cap_eq_op_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'Capital($)_x', 'Capital($)_y']]])
    cap_df = cap_df.sort_values(by=['TradeGroup', 'FundCode']).rename(columns={'Capital($)_x':'Capital($)_NP', 'Capital($)_y':'Capital($)_Eze'})
    cap_df['T/F'] = abs((cap_df['Capital($)_NP']-cap_df['Capital($)_Eze'])/(cap_df['Capital($)_Eze'])) <= 0.03
    cap_df = cap_df[cap_df['T/F'] == False].sort_values(by=['TradeGroup', 'FundCode'])
    cap_df = cap_df[pd.notnull(cap_df['Capital($)_NP'])|pd.notnull(cap_df['Capital($)_Eze'])]
    cap_df.to_excel('C:/Users/aduprey/Desktop/cap_05_15.xlsx')

    mktcapcat_bonds_df = bonds_df[['Date', 'FundCode', 'BloombergGID', 'TradeGroup', 'Ticker_x', 'Ticker_y', 'MarketCapCategory_x', 'MarketCapCategory_y']]
    mktcapcat_bonds_df = mktcapcat_bonds_df.rename(columns={'Ticker_x':'Ticker'})
    mktcapcat_eq_op_df = equity_options_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'MarketCapCategory_x', 'MarketCapCategory_y']]
    mktcapcat_df = pd.concat([mktcapcat_bonds_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'MarketCapCategory_x', 'MarketCapCategory_y']], mktcapcat_eq_op_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'MarketCapCategory_x', 'MarketCapCategory_y']]])
    mktcapcat_df = mktcapcat_df.sort_values(by=['TradeGroup', 'FundCode']).rename(columns={'MarketCapCategory_x':'MarketCapCategory_NP', 'MarketCapCategory_y':'MarketCapCategory_Eze'})
    mktcapcat_df['T/F'] = (mktcapcat_df['MarketCapCategory_NP'] == mktcapcat_df['MarketCapCategory_Eze'])
    mktcapcat_df = mktcapcat_df[mktcapcat_df['T/F'] == False].sort_values(by=['TradeGroup', 'FundCode'])
    mktcapcat_df.to_excel('C:/Users/aduprey/Desktop/marketCapCategory_05_15.xlsx')

    industry_bonds_df = bonds_df[['Date', 'FundCode', 'BloombergGID', 'TradeGroup', 'Ticker_x', 'Ticker_y', 'Industry_x', 'Industry_y']]
    industry_bonds_df = industry_bonds_df.rename(columns={'Ticker_x':'Ticker'})
    industry_eq_op_df = equity_options_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'Industry_x', 'Industry_y']]
    industry_df = pd.concat([industry_bonds_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'Industry_x', 'Industry_y']], industry_eq_op_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'Industry_x', 'Industry_y']]])
    industry_df = industry_df.sort_values(by=['TradeGroup', 'FundCode']).rename(columns={'Industry_x':'Industry_NP', 'Industry_y':'Industry_Eze'})
    industry_df['T/F'] = (industry_df['Industry_NP'] == industry_df['Industry_Eze'])
    industry_df = industry_df[industry_df['T/F'] == False].sort_values(by=['TradeGroup', 'FundCode'])
    industry_df.to_excel('C:/Users/aduprey/Desktop/Industry_05_15.xlsx')

    sector_bonds_df = bonds_df[['Date', 'FundCode', 'BloombergGID', 'TradeGroup', 'Ticker_x', 'Ticker_y', 'Sector_x', 'Sector_y']]
    sector_bonds_df = sector_bonds_df.rename(columns={'Ticker_x':'Ticker'})
    sector_eq_op_df = equity_options_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'Sector_x', 'Sector_y']]
    sector_df = pd.concat([sector_bonds_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'Sector_x', 'Sector_y']], sector_eq_op_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'Sector_x', 'Sector_y']]])
    sector_df = sector_df.sort_values(by=['TradeGroup', 'FundCode']).rename(columns={'Sector_x':'Sector_NP', 'Sector_y':'Sector_Eze'})
    sector_df['T/F'] = (sector_df['Sector_NP'] == sector_df['Sector_Eze'])
    sector_df = sector_df[sector_df['T/F'] == False].sort_values(by=['TradeGroup', 'FundCode'])
    sector_df.to_excel('C:/Users/aduprey/Desktop/sector_05_15.xlsx')

    longshort_bonds_df = bonds_df[['Date', 'FundCode', 'BloombergGID', 'TradeGroup', 'Ticker_x', 'Ticker_y', 'LongShort_x', 'LongShort_y']]
    longshort_bonds_df = longshort_bonds_df.rename(columns={'Ticker_x':'Ticker'})
    longshort_eq_op_df = equity_options_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'LongShort_x', 'LongShort_y']]
    longshort_df = pd.concat([longshort_bonds_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'LongShort_x', 'LongShort_y']], longshort_eq_op_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'LongShort_x', 'LongShort_y']]])
    longshort_df = longshort_df.sort_values(by=['TradeGroup', 'FundCode']).rename(columns={'LongShort_x':'LongShort_NP', 'LongShort_y':'LongShort_Eze'})
    longshort_df['T/F'] = (longshort_df['LongShort_NP'] == longshort_df['LongShort_Eze'])
    longshort_df = longshort_df[longshort_df['T/F'] == False].sort_values(by=['TradeGroup', 'FundCode'])
    longshort_df.to_excel('C:/Users/aduprey/Desktop/longshort_05_15.xlsx')

    cr01_bonds_df = bonds_df[['Date', 'FundCode', 'BloombergGID', 'TradeGroup', 'Ticker_x', 'Ticker_y', 'CR01_x', 'CR01_y', 'DV01_x', 'DV01_y', 'Adj_CR01_x', 'Adj_CR01_y']]
    cr01_bonds_df = cr01_bonds_df.rename(columns={'Ticker_x':'Ticker'})
    cr01_eq_op_df = equity_options_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'CR01_x', 'CR01_y', 'DV01_x', 'DV01_y', 'Adj_CR01_x', 'Adj_CR01_y']]
    cr01_df = pd.concat([cr01_bonds_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'CR01_x', 'CR01_y', 'DV01_x', 'DV01_y', 'Adj_CR01_x', 'Adj_CR01_y']], cr01_eq_op_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'CR01_x', 'CR01_y', 'DV01_x', 'DV01_y', 'Adj_CR01_x', 'Adj_CR01_y']]])
    cr01_df = cr01_df.sort_values(by=['TradeGroup', 'FundCode']).rename(columns={'CR01_x':'CR01_NP', 'CR01_y':'CR01_Eze', 'DV01_x':'DV01_NP', 'DV01_y':'DV01_Eze', 'Adj_CR01_x':'Adj_CR01_NP', 'Adj_CR01_y':'Adj_CR01_Eze'})
    cr01_df['cr01_T/F'] = (cr01_df['CR01_NP']== cr01_df['CR01_Eze'])
    cr01_df['dv01_T/F'] = (cr01_df['DV01_NP']==cr01_df['DV01_Eze'])
    cr01_df['adj_cr01_T/F'] = (cr01_df['Adj_CR01_NP']==cr01_df['Adj_CR01_Eze'])
    cr01_df = cr01_df[(cr01_df['cr01_T/F'] == False)|(cr01_df['dv01_T/F'] == False)|(cr01_df['adj_cr01_T/F'] == False)].sort_values(by=['TradeGroup', 'FundCode'])
    cr01_df.to_excel('C:/Users/aduprey/Desktop/CR01_05_15.xlsx')

    bonds_df = bonds_df[(bonds_df.AlphaHedge_x == "Alpha")|(bonds_df.AlphaHedge_x == "Alpha")]
    equity_options_df = equity_options_df[(equity_options_df.AlphaHedge_x == "Alpha")|(equity_options_df.AlphaHedge_x == "Alpha")]
    dealVal_bonds_df = bonds_df[['Date', 'FundCode', 'BloombergGID', 'TradeGroup', 'Ticker_x', 'Ticker_y', 'DealValue_x', 'DealValue_y']]
    dealVal_bonds_df = dealVal_bonds_df.rename(columns={'Ticker_x':'Ticker'})
    dealVal_eq_op_df = equity_options_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'DealValue_x', 'DealValue_y']]
    dealVal_df = pd.concat([dealVal_bonds_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'DealValue_x', 'DealValue_y']], dealVal_eq_op_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'DealValue_x', 'DealValue_y']]])
    dealVal_df = dealVal_df.sort_values(by=['TradeGroup', 'FundCode']).rename(columns={'DealValue_x':'DealValue_NP', 'DealValue_y':'DealValue_Eze'})
    dealVal_df['DealValue_NP'] = dealVal_df['DealValue_NP'].astype(float)
    dealVal_df['T/F'] = abs((dealVal_df['DealValue_NP']-dealVal_df['DealValue_Eze'])/(dealVal_df['DealValue_Eze'])) <= 0.01
    dealVal_df = dealVal_df[dealVal_df['T/F'] == False].sort_values(by=['TradeGroup', 'FundCode'])
    dealVal_df = dealVal_df[(dealVal_df['DealValue_NP'] != 0)|(dealVal_df['DealValue_Eze'] != 0)]
    dealVal_df.to_excel('C:/Users/aduprey/Desktop/DealValue_05_15.xlsx')
    
    catalyst_bonds_df = bonds_df[['Date', 'FundCode', 'BloombergGID', 'TradeGroup', 'Ticker_x', 'Ticker_y', 'CatalystName_x', 'CatalystName_y']]
    catalyst_bonds_df = catalyst_bonds_df.rename(columns={'Ticker_x':'Ticker'})
    catalyst_eq_op_df = equity_options_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'CatalystName_x', 'CatalystName_y']]
    catalyst_df = pd.concat([catalyst_bonds_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'CatalystName_x', 'CatalystName_y']], catalyst_eq_op_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'CatalystName_x', 'CatalystName_y']]])
    catalyst_df = catalyst_df.sort_values(by=['TradeGroup', 'FundCode']).rename(columns={'CatalystName_x':'CatalystName_NP', 'CatalystName_y':'CatalystName_Eze'})
    catalyst_df['T/F'] = (catalyst_df['CatalystName_NP'] == catalyst_df['CatalystName_Eze'])
    catalyst_df = catalyst_df[catalyst_df['T/F'] == False].sort_values(by=['TradeGroup', 'FundCode'])
    catalyst_df.to_excel('C:/Users/aduprey/Desktop/CatalystName_05_15.xlsx')
    
    bucket_bonds_df = bonds_df[['Date', 'FundCode', 'BloombergGID', 'TradeGroup', 'Ticker_x', 'Ticker_y', 'Bucket_x', 'Bucket_y']]
    bucket_bonds_df = bucket_bonds_df.rename(columns={'Ticker_x':'Ticker'})
    bucket_eq_op_df = equity_options_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'Bucket_x', 'Bucket_y']]
    bucket_df = pd.concat([bucket_bonds_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'Bucket_x', 'Bucket_y']], bucket_eq_op_df[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'Bucket_x', 'Bucket_y']]])
    bucket_df = bucket_df.sort_values(by=['TradeGroup', 'FundCode']).rename(columns={'Bucket_x':'Bucket_NP', 'Bucket_y':'Bucket_Eze'})
    bucket_df['T/F'] = (bucket_df['Bucket_NP'] == bucket_df['Bucket_Eze'])
    bucket_df = bucket_df[bucket_df['T/F'] == False].sort_values(by=['TradeGroup', 'FundCode'])
    bucket_df.to_excel('C:/Users/aduprey/Desktop/Bucket_05_15.xlsx')

    print('Finished Generating the Files')

In [16]:
generate_files(PCVH_new, df_flat_file_new)

Finished Generating the Files


In [35]:
df_flat_file_new.head()

Unnamed: 0        Date FundCode      TradeGroup TradeGroup_Tradar_Name  \
0           0  2019-05-15      AED  AABA R/R SHORT         AABA R/R SHORT   
1           1  2019-05-15      AED  AABA R/R SHORT         AABA R/R SHORT   
2           2  2019-05-15      CAM  AABA R/R SHORT         AABA R/R SHORT   
3           3  2019-05-15      CAM  AABA R/R SHORT         AABA R/R SHORT   
4           4  2019-05-15       LG  AABA R/R SHORT         AABA R/R SHORT   

                      Sleeve      Bucket  TradeGroupId   Ticker  \
0  Equity Special Situations  Re-Ratings             1  AABA US   
1  Equity Special Situations  Re-Ratings             1  BABA US   
2  Equity Special Situations  Re-Ratings             1  AABA US   
3  Equity Special Situations  Re-Ratings             1  BABA US   
4  Equity Special Situations  Re-Ratings             1  AABA US   

  BloombergGlobalId  BloombergGID         BBGID SecType MarketCapCategory  \
0      BBG000GFFQN9  BBG000GFFQN9  BBG000GFFQN9      EQ         Large Cap   
1      BBG006G2JVL2  BBG006G2JVL2  BBG006G2JVL2      EQ         Large Cap   
2      BBG000GFFQN9  BBG000GFFQN9  BBG000GFFQN9      EQ         Large Cap   
3      BBG006G2JVL2  BBG006G2JVL2  BBG006G2JVL2      EQ         Large Cap   
4      BBG000GFFQN9  BBG000GFFQN9  BBG000GFFQN9      EQ         Large Cap   

   SecurityId  DealTermsCash  DealTermsStock  DealValue DealClosingDate  \
0         NaN            0.0             0.0        0.0      2019-12-31   
1         NaN            0.0             0.0        0.0      2019-12-31   
2         NaN            0.0             0.0        0.0      2019-12-31   
3         NaN            0.0             0.0        0.0      2019-12-31   
4         NaN            0.0             0.0        0.0      2019-12-31   

   Equity_Risk_Factor  DV01  CR01  Adj_CR01 UltimateCountry AlphaHedge  \
0                 1.0   0.0   0.0       0.0              US      Alpha   
1                 1.0   0.0   0.0       0.0              CN      Hedge   
2                 1.0   0.0   0.0       0.0              US      Alpha   
3                 1.0   0.0   0.0       0.0              CN      Hedge   
4                 1.0   0.0   0.0       0.0              US      Alpha   

   Exposure_Long  Exposure_Short  Exposure_Net  Exposure_Net(%)     NetMktVal  \
0            0.0      -489397.84    -489397.84        -0.386685 -4.893978e+05   
1       427660.8            0.00     427660.80         0.337905  4.276608e+05   
2            0.0      -481623.96    -481623.96        -0.371683 -4.816240e+05   
3       420734.4            0.00     420734.40         0.324693  4.207344e+05   
4            0.0     -1399441.04   -1399441.04        -0.403879 -1.399441e+06   

     Capital($)  Capital(%)  BaseCaseNavImpact  OutlierNavImpact      Qty  \
0  4.893978e+05    0.386685              12.91             38.67  -6862.0   
1           NaN         NaN             -33.79            -33.79   2408.0   
2  4.816240e+05    0.371683              12.41             37.17  -6753.0   
3           NaN         NaN             -32.47            -32.47   2369.0   
4  1.399441e+06    0.403879              13.49             40.39 -19622.0   

  LongShort                  Sector                   Industry  \
0     Short  CONSUMER DISCRETIONARY  INTERNET & CATALOG RETAIL   
1     Short  CONSUMER DISCRETIONARY  INTERNET & CATALOG RETAIL   
2     Short  CONSUMER DISCRETIONARY  INTERNET & CATALOG RETAIL   
3     Short  CONSUMER DISCRETIONARY  INTERNET & CATALOG RETAIL   
4     Short  CONSUMER DISCRETIONARY  INTERNET & CATALOG RETAIL   

   CatalystRating CatalystName     Fund_NAV Analyst  Equity_Risk_Exp  \
0               1         Soft  126562452.7      TC       -489397.84   
1               1         Soft  126562452.7      TC        427660.80   
2               1         Soft  129579197.6      TC       -481623.96   
3               1         Soft  129579197.6      TC        420734.40   
4               1         Soft  346500156.4      TC      -1399441.04   

In [10]:
PCVH_new['TradeGroup'] = PCVH_new['TradeGroup'].apply(lambda x: x.upper())
df_flat_file_new['TradeGroup'] = df_flat_file_new['TradeGroup'].apply(lambda x: x.upper())
PCVH_new = PCVH_new[PCVH_new.SecType != 'FxFwd']
df_flat_file_new = df_flat_file_new[df_flat_file_new.SecType != 'FXFWD']
PCVH_new['Date'] = PCVH_new['Date'].apply(lambda x: x.strftime('%Y-%m-%d'))
df_flat_file_new = df_flat_file_new[df_flat_file_new.FundCode != 'ETF1']
df_flat_file_new = df_flat_file_new[df_flat_file_new.FundCode != 'ETF2']
df_flat_file_new = df_flat_file_new[df_flat_file_new.FundCode != 'ETF3']
df_flat_file_new = df_flat_file_new[df_flat_file_new.FundCode != 'INDEX1']
df_flat_file_new = df_flat_file_new[df_flat_file_new.FundCode != 'INDEX2']
df_flat_file_new = df_flat_file_new[df_flat_file_new.FundCode != 'INDEX3']

In [24]:
print(len(PCVH_new))
print(len(df_flat_file_new))

1166
1167


In [25]:
pcvh_new = PCVH_new#[PCVH_new.FundCode == 'ARB']
f_new = df_flat_file_new#[df_flat_file_new.FundCode == 'ARB']

In [26]:
cols = ['Date', 'FundCode', 'TradeGroup', 'BloombergGID', 'Ticker_x', 'Ticker_y', 'TradeGroup_Tradar_Name_x', 'TradeGroup_Tradar_Name_y',
       'Sleeve_x', 'Sleeve_y', 'Bucket_x', 'Bucket_y', 'TradeGroupId_x', 'TradeGroupId_y',
       'BloombergGlobalId_x', 'BloombergGlobalId_y', 'BBGID_x', 'BBGID_y', 'SecType_x', 'SecType_y',
       'MarketCapCategory_x', 'MarketCapCategory_y', 'SecurityId_x', 'SecurityId_y', 'DealTermsCash_x', 'DealTermsCash_y',
       'DealTermsStock_x', 'DealTermsStock_y', 'DealValue_x', 'DealValue_y', 'DealClosingDate_x', 'DealClosingDate_y',
       'Equity_Risk_Factor_x', 'Equity_Risk_Factor_y', 'DV01_x', 'DV01_y', 'CR01_x', 'CR01_y', 'Adj_CR01_x', 'Adj_CR01_y',
       'UltimateCountry_x', 'UltimateCountry_y', 'AlphaHedge_x', 'AlphaHedge_y', 'Exposure_Long_x', 'Exposure_Long_y',
       'Exposure_Short_x', 'Exposure_Short_y', 'Exposure_Net_x', 'Exposure_Net_y', 'Exposure_Net(%)_x', 'Exposure_Net(%)_y',
       'NetMktVal_x', 'NetMktVal_y', 'Capital($)_x', 'Capital($)_y', 'Capital(%)_x', 'Capital(%)_y',
       'BaseCaseNavImpact_x', 'BaseCaseNavImpact_y', 'OutlierNavImpact_x', 'OutlierNavImpact_y', 'Qty_x', 'Qty_y', 'LongShort_x',
       'LongShort_y', 'Sector_x', 'Sector_y', 'Industry_x', 'Industry_y', 'CatalystRating_x', 'CatalystRating_y', 'CatalystName_x',
       'CatalystName_y', 'Fund_NAV_x', 'Fund_NAV_y', 'Equity_Risk_Exp_x', 'Equity_Risk_Exp_y', 'DealDuration_x', 'DealDuration_y']

In [27]:
resulting_new = pd.merge(pcvh_new, f_new, how = 'outer', on=['Date', 'FundCode', 'TradeGroup', 'BloombergGID'])
r_new = resulting_new[cols]
r_new.sort_values(by=['TradeGroup'])

Date FundCode                          TradeGroup  \
599   2019-05-06      WED                      AABA R/R SHORT   
534   2019-05-06      AED                      AABA R/R SHORT   
743   2019-05-06      TAQ                      AABA R/R SHORT   
604   2019-05-06      TAQ                      AABA R/R SHORT   
200   2019-05-06       LG                      AABA R/R SHORT   
98    2019-05-06      CAM                      AABA R/R SHORT   
1021  2019-05-06      WED                      AABA R/R SHORT   
228   2019-05-06       LG                      AABA R/R SHORT   
810   2019-05-06      AED                      AABA R/R SHORT   
105   2019-05-06      CAM                      AABA R/R SHORT   
796   2019-05-06      TAQ                            ACOR R/R   
797   2019-05-06      TAQ                            ACOR R/R   
542   2019-05-06      TAQ                            ACOR R/R   
508   2019-05-06      TAQ                            ACOR R/R   
659   2019-05-06      LEV                           ADSW - WM   
964   2019-05-06      ARB                           ADSW - WM   
162   2019-05-06      CAM                           ADSW - WM   
382   2019-05-06      AED                           ADSW - WM   
189   2019-05-06     MALT                           ADSW - WM   
217   2019-05-06       LG                           ADSW - WM   
755   2019-05-06     MACO                           ADSW - WM   
1166  2019-05-06      ARB                               AEDNX   
384   2019-05-06      ARB                               AEDNX   
989   2019-05-06      TAQ                            AIMC R/R   
977   2019-05-06      TAQ                            AIMC R/R   
467   2019-05-06      TAQ                            AIMC R/R   
470   2019-05-06      TAQ                            AIMC R/R   
935   2019-05-06      TAQ                            AIMC R/R   
464   2019-05-06      TAQ                       ALV R/R SHORT   
62    2019-05-06      CAM                       ALV R/R SHORT   
52    2019-05-06      CAM                       ALV R/R SHORT   
457   2019-05-06       LG                       ALV R/R SHORT   
458   2019-05-06       LG                       ALV R/R SHORT   
816   2019-05-06      WED                       ALV R/R SHORT   
787   2019-05-06      AED                       ALV R/R SHORT   
788   2019-05-06      AED                       ALV R/R SHORT   
419   2019-05-06      AED                       ALV R/R SHORT   
1167  2019-05-06      AED                       ALV R/R SHORT   
1117  2019-05-06      CAM                       ALV R/R SHORT   
378   2019-05-06       LG                       ALV R/R SHORT   
976   2019-05-06      TAQ                       ALV R/R SHORT   
1088  2019-05-06      WED                       ALV R/R SHORT   
180   2019-05-06       LG                       ALV R/R SHORT   
169   2019-05-06       LG                       ALV R/R SHORT   
786   2019-05-06      AED                       ALV R/R SHORT   
46    2019-05-06      CAM                       ALV R/R SHORT   
1137  2019-05-06      AED                       ALV R/R SHORT   
1169  2019-05-06       LG                       ALV R/R SHORT   
598   2019-05-06      TAQ                       ALV R/R SHORT   
13    2019-05-06      CAM                       ALV R/R SHORT   
1168  2019-05-06      CAM                       ALV R/R SHORT   
690   2019-05-06      WED                       ALV R/R SHORT   
549   2019-05-06      WED                       ALV R/R SHORT   
526   2019-05-06      TAQ                       ALV R/R SHORT   
495   2019-05-06      TAQ                       ALV R/R SHORT   
557   2019-05-06      WED                       ALV R/R SHORT   
1170  2019-05-06      TAQ                       ALV R/R SHORT   
1171  2019-05-06      WED                       ALV R/R SHORT   
374   2019-05-06     MALT                           APC - CVX   
656   2019-05-06     MACO                           APC - CVX   
984   2019-05-06      ARB                      

In [28]:
len(r_new)

1200

In [29]:
#t_new = r_new[['Date', 'FundCode', 'TradeGroup', 'Ticker', 'Sleeve_x', 'AlphaHedge_x', 'SecType_x', 'DealTermsCash_x', 'DealTermsCash_y', 'DealTermsStock_x', 'DealTermsStock_y', 'DealValue_x', 'DealValue_y', 'Equity_Risk_Factor_x', 'Equity_Risk_Factor_y', 'Exposure_Net_x', 'Exposure_Net_y', 'Equity_Risk_Exp_x', 'Equity_Risk_Exp_y']]#, 'Capital($)_x', 'Capital($)_y']] #, 'Qty_x', 'Qty_y']]
#t_new['Capital($)_x'] = t_new['Capital($)_x'].round(0)
#t_new['T/F_d'] = t_new['DealTermsCash_x'] == t_new['DealTermsCash_y']
#t_new['T/F_ds'] = t_new['DealTermsStock_x'] == t_new['DealTermsStock_y']
#t_new['T/F_dv'] = t_new['DealValue_x'] == t_new['DealValue_y']
#t_new['T/F_e'] = t_new['Equity_Risk_Factor_x'] == t_new['Equity_Risk_Factor_y']
#t_new['T/F_exp'] = abs((t_new['Exposure_Net_x']-t_new['Exposure_Net_y'])/(t_new['Exposure_Net_y'])) <= 0.01
#t_new['T/F'] = abs((t_new['Equity_Risk_Exp_x']-t_new['Equity_Risk_Exp_y'])/(t_new['Equity_Risk_Exp_y'])) <= 0.01

#t_new['T/F'] = t_new['Capital($)_x'] == t_new['Capital($)_y']
#t_new = t_new[(t_new['T/F'] == False)|(t_new['T/F_exp'] == False)]

In [47]:
np_data = PCVH_new
eze_data = df_flat_file_new

In [31]:
t = r_new[['Date', 'FundCode', 'TradeGroup', 'BloombergGID', 'Ticker_x', 'Ticker_y', 'AlphaHedge_x', 'AlphaHedge_y', 'Capital($)_x', 'Capital($)_y']]#, "Qty_x", "Qty_y"]]
t = t.sort_values(by='TradeGroup').round(2) #"DealTermsCash_x", 'DealTermsCash_y', 'DealTermsStock_x', 'DealTermsStock_y', 'DealValue_x', 'DealValue_y',
#t['Capital($)_x'] = t['Capital($)_x'].round()
#t['cap_T/F'] = t['Capital($)_x'] == t['Capital($)_y']
#t['dv01_T/F'] = t['DV01_x'] == t['DV01_y']
#t['cr01_T/F'] = t['CR01_x'] == t['CR01_y']
#t['adcr_T/F'] = t['Adj_CR01_x'] == t['Adj_CR01_y']
#t['exp_T/F'] = abs((t['Exposure_Net_x']-t['Exposure_Net_y'])/(t['Exposure_Net_y'])) <= 0.05
#t['dc_T/F'] = abs((t['DealTermsCash_x'].astype(float)-t['DealTermsCash_y'])/(t['DealTermsCash_y'])) <= 0.01
#t['ds_T/F'] = abs((t['DealTermsStock_x'].astype(float)-t['DealTermsStock_y'])/(t['DealTermsStock_y'])) <= 0.01
#t['dv_T/F'] = abs((t['DealValue_x'].astype(float)-t['DealValue_y'])/(t['DealValue_y'])) <= 0.01
t['cap_T/F'] = abs((t['Capital($)_x']-t['Capital($)_y'])/(t['Capital($)_y'])) <= 0.03
#t['qty_T/F'] = t['Qty_x'] == t['Qty_y']
#t = t[(t['cap_T/F'] == False)|(t['exp_T/F'] == False)]
t = t[(t['cap_T/F'] == False)]#|(t['cap_T/F'] == False)|(t['dv_T/F'] == False)]#|(t['dc_T/F'] == False)|(t['ds_T/F'] == False)|(t['dv_T/F'] == False)|(t['cap_T/F'] == False)|(t['qty_T/F'] == False)]

C:\Users\aduprey\AppData\Local\Continuum\anaconda3\envs\Python3Env\lib\site-packages\pandas\core\series.py:1828: RuntimeWarning: invalid value encountered in rint
  result = com._values_from_object(self).round(decimals)


In [43]:
t = t.rename(columns={'Exposure_Net_x': 'Exposure_Net_NP', 'Exposure_Net_y': 'Exposure_Net_Eze'})
#t = t[(t.Ticker ==  "QQQ US 05/03/19 P187")|(t.Ticker ==  "CNX US")|(t.Ticker ==  "CLD 12 11/01/21")|(t.Ticker ==  "AI FP SWAP")|(t.Ticker ==  "AI FP MS Swap")]
t = t.sort_values(by=['TradeGroup', 'FundCode']).round(2)
t = t[(t['Capital($)_x'].notnull())|(t['Capital($)_y'].notnull())]
t

Date FundCode                 TradeGroup        BloombergGID  \
1166  2019-05-06      ARB                      AEDNX           03875R403   
384   2019-05-06      ARB                      AEDNX        BBG0016YWRY4   
1155  2019-05-06      LEV                  APC - CVX        BBG00NWPSNP0   
1030  2019-05-06      TAQ                   ARMK R/R        BBG00NXGTFV8   
966   2019-05-06      TAQ                   AVYA R/R        BBG00NLRT1D8   
232   2019-05-06      AED                  CBSTZ S/S  EQ0515259401286252   
1175  2019-05-06      AED                  CBSTZ S/S        BBG000GZD660   
1176  2019-05-06      ARB                  CBSTZ S/S        BBG000GZD660   
633   2019-05-06      ARB                  CBSTZ S/S  EQ0515259401286252   
1177  2019-05-06      WIC                  CBSTZ S/S        BBG000GZD660   
1082  2019-05-06      WIC                  CBSTZ S/S  EQ0515259401286252   
1083  2019-05-06      WED     CLD BONDS CONV - TRADE        BBG00F0GDKY4   
257   2019-05-06     TACO        CREDIT MACRO HEDGES        BBG000NXDKM8   
927   2019-05-06      AED             DOLE - MURDOCK                None   
1178  2019-05-06      AED             DOLE - MURDOCK            DOLE LIT   
876   2019-05-06      ARB             DOLE - MURDOCK                None   
1179  2019-05-06      ARB             DOLE - MURDOCK            DOLE LIT   
1180  2019-05-06      CAM             DOLE - MURDOCK            DOLE LIT   
94    2019-05-06      CAM             DOLE - MURDOCK                None   
1181  2019-05-06       LG             DOLE - MURDOCK            DOLE LIT   
177   2019-05-06       LG             DOLE - MURDOCK                None   
555   2019-05-06      WIC             DOLE - MURDOCK                None   
1182  2019-05-06      WIC             DOLE - MURDOCK            DOLE LIT   
834   2019-05-06      AED              DOW R/R SHORT        BBG000BHBK84   
1183  2019-05-06      AED              DOW R/R SHORT        BBG00BN96922   
108   2019-05-06      CAM              DOW R/R SHORT        BBG000BHBK84   
1184  2019-05-06      CAM              DOW R/R SHORT        BBG00BN96922   
222   2019-05-06       LG              DOW R/R SHORT        BBG000BHBK84   
1185  2019-05-06       LG              DOW R/R SHORT        BBG00BN96922   
1186  2019-05-06      TAQ              DOW R/R SHORT        BBG00BN96922   
523   2019-05-06      TAQ              DOW R/R SHORT        BBG000BHBK84   
558   2019-05-06      WED              DOW R/R SHORT        BBG000BHBK84   
1187  2019-05-06      WED              DOW R/R SHORT        BBG00BN96922   
1188  2019-05-06     TACO          ISATLN 4.875 2022           EK2884691   
843   2019-05-06     TACO          ISATLN 4.875 2022        BBG006JMSYZ4   
512   2019-05-06      TAQ                   JACK S/S        BBG00MB2R1T1   
1029  2019-05-06      TAQ                   JACK S/S        BBG000GZYVY1   
527   2019-05-06      ARB                 MEG - NXST                None   
1190  2019-05-06      ARB                 MEG - NXST             MEG CVR   
754   2019-05-06      AED                MLNX - NVDA        BBG00M960061   
920   2019-05-06      ARB                MLNX - NVDA        BBG00M960061   
88    2019-05-06      CAM                MLNX - NVDA        BBG00M960061   
1153  2019-05-06      LEV                MLNX - NVDA        BBG00M960061   
580   2019-05-06      LEV                MLNX - NVDA        BBG00N4BXDC2   
216   2019-05-06       LG                MLNX - NVDA        BBG00M960061   
1085  2019-05-06     MACO                MLNX - NVDA        BBG00M960061   
256   2019-05-06     MALT                MLNX - NVDA        BBG00M960061   
586   2019-05-06      LEV             NEM CONVICTION        BBG00NCR17V5   
665   2019-05-06      LEV             NEM CONVICTION        BBG00NQZFXG7   
1087  2019-05-06      LEV             NEM CONVICTION        BBG00NQZFYH4   
1005  2019-05-06      LEV             NEM CONVICTION        BBG00NQZFWD2   
302   2019-05-06     TACO              PRTK CONVERTS        

In [44]:
len(t)

107

In [17]:
PCVH_new[(PCVH_new.TradeGroup == 'APC - OXY')&(PCVH_new.FundCode == 'LEV')].sort_values(by=['FundCode', 'Ticker'])

Date FundCode TradeGroup TradeGroup_Tradar_Name            Sleeve  \
735   2019-05-16      LEV  APC - OXY              APC - OXY  Merger Arbitrage   
770   2019-05-16      LEV  APC - OXY              APC - OXY  Merger Arbitrage   
1153  2019-05-16      LEV  APC - OXY              APC - OXY  Merger Arbitrage   
635   2019-05-16      LEV  APC - OXY              APC - OXY  Merger Arbitrage   
793   2019-05-16      LEV  APC - OXY              APC - OXY  Merger Arbitrage   
714   2019-05-16      LEV  APC - OXY              APC - OXY  Merger Arbitrage   
611   2019-05-16      LEV  APC - OXY              APC - OXY  Merger Arbitrage   
466   2019-05-16      LEV  APC - OXY              APC - OXY  Merger Arbitrage   
636   2019-05-16      LEV  APC - OXY              APC - OXY  Merger Arbitrage   
612   2019-05-16      LEV  APC - OXY              APC - OXY  Merger Arbitrage   
1154  2019-05-16      LEV  APC - OXY              APC - OXY  Merger Arbitrage   
774   2019-05-16      LEV  APC - OXY              APC - OXY  Merger Arbitrage   
652   2019-05-16      LEV  APC - OXY              APC - OXY  Merger Arbitrage   
1049  2019-05-16      LEV  APC - OXY              APC - OXY  Merger Arbitrage   

         Bucket  TradeGroupId                 Ticker BloombergGlobalId  \
735   Optimized       94923.0                 APC US      BBG000BC40Y8   
770   Optimized       94923.0    APC US 05/17/19 C65              None   
1153  Optimized       94923.0  APC US 05/17/19 C72.5              None   
635   Optimized       94923.0    APC US 05/17/19 P70              None   
793   Optimized       94923.0    APC US 07/19/19 C75              None   
714   Optimized       94923.0    APC US 07/19/19 P70              None   
611   Optimized       94923.0    APC US 07/19/19 P75              None   
466   Optimized       94923.0                 CVX US      BBG000K4ND22   
636   Optimized       94923.0                 CVX US      BBG000K4ND22   
612   Optimized       94923.0   CVX US 05/17/19 P115              None   
1154  Optimized       94923.0                 OXY US      BBG000BQQ2S6   
774   Optimized       94923.0    OXY US 05/17/19 C57              None   
652   Optimized       94923.0  OXY US 05/17/19 C57.5              None   
1049  Optimized       94923.0    OXY US 05/17/19 C58              None   

      BloombergGID         BBGID  SecType MarketCapCategory  SecurityId  \
735   BBG000BC40Y8  BBG000BC40Y8       EQ         Large Cap     79836.0   
770   BBG00M1GKT62  BBG00M1GKT62  ExchOpt         Large Cap     94724.0   
1153  BBG00M1GKXB7  BBG00M1GKXB7  ExchOpt         Large Cap     94797.0   
635   BBG00M1GKW83  BBG00M1GKW83  ExchOpt         Large Cap     94833.0   
793   BBG00NWPSPW7  BBG00NWPSPW7  ExchOpt         Large Cap     94822.0   
714   BBG00NWPSNP0  BBG00NWPSNP0  ExchOpt         Large Cap     94814.0   
611   BBG00NWPSPV8  BBG00NWPSPV8  ExchOpt         Large Cap     94893.0   
466   BBG000K4ND22  BBG000K4ND22       EQ         Large Cap     94720.0   
636   BBG000K4ND22  BBG000K4ND22       EQ         Large Cap     94720.0   
612   BBG00NC3M2H2  BBG00NC3M2H2  ExchOpt         Large Cap     94812.0   
1154  BBG000BQQ2S6  BBG000BQQ2S6       EQ         Large Cap     94742.0   
774   BBG00NYGND02  BBG00NYGND02  ExchOpt         Large Cap     94916.0   
652   BBG00MFH6JL6  BBG00MFH6JL6  ExchOpt         Large Cap     94917.0   
1049  BBG00NYGNF43  BBG00NYGNF43  ExchOpt         Large Cap     94918.0   

     DealTermsCash DealTermsStock DealValue DealClosingDate  \
735        59.0000        15.7702   74.9337      2019-09-01   
770        59.0000        15.7702   74.9337      2019-09-01   
1153       59.0000        15.7702   74.9337      2019-09-01   
635        59.0000        15.7702   74.9337      2019-09-01   
793        59.0000        15.7702   74.9337      2019-09-01   
714        59.0000        15.7702   74.9337      2019-09-01   
611        59.0000        15.7702   74.9337      2019-09-01   
466        59.0000        15.7702   74.9337      2019-0

In [18]:
df_flat_file_new[(df_flat_file_new.TradeGroup == 'APC - OXY')&(df_flat_file_new.FundCode == 'LEV')].sort_values(by=['FundCode', 'Ticker'])

Unnamed: 0        Date FundCode TradeGroup TradeGroup_Tradar_Name  \
70          70  2019-05-16      LEV  APC - OXY              APC - OXY   
64          64  2019-05-16      LEV  APC - OXY              APC - OXY   
65          65  2019-05-16      LEV  APC - OXY              APC - OXY   
66          66  2019-05-16      LEV  APC - OXY              APC - OXY   
67          67  2019-05-16      LEV  APC - OXY              APC - OXY   
68          68  2019-05-16      LEV  APC - OXY              APC - OXY   
69          69  2019-05-16      LEV  APC - OXY              APC - OXY   
71          71  2019-05-16      LEV  APC - OXY              APC - OXY   
75          75  2019-05-16      LEV  APC - OXY              APC - OXY   
73          73  2019-05-16      LEV  APC - OXY              APC - OXY   
72          72  2019-05-16      LEV  APC - OXY              APC - OXY   
74          74  2019-05-16      LEV  APC - OXY              APC - OXY   

              Sleeve     Bucket  TradeGroupId                 Ticker  \
70  Merger Arbitrage  Optimized             1                 APC US   
64  Merger Arbitrage  Optimized             1    APC US 05/17/19 C65   
65  Merger Arbitrage  Optimized             1  APC US 05/17/19 C72.5   
66  Merger Arbitrage  Optimized             1    APC US 05/17/19 P70   
67  Merger Arbitrage  Optimized             1    APC US 07/19/19 C75   
68  Merger Arbitrage  Optimized             1    APC US 07/19/19 P70   
69  Merger Arbitrage  Optimized             1    APC US 07/19/19 P75   
71  Merger Arbitrage  Optimized             1   CVX US 05/17/19 P115   
75  Merger Arbitrage  Optimized             1                 OXY US   
73  Merger Arbitrage  Optimized             1    OXY US 05/17/19 C57   
72  Merger Arbitrage  Optimized             1  OXY US 05/17/19 C57.5   
74  Merger Arbitrage  Optimized             1    OXY US 05/17/19 C58   

   BloombergGlobalId  BloombergGID         BBGID  SecType MarketCapCategory  \
70      BBG000BC40Y8  BBG000BC40Y8  BBG000BC40Y8       EQ         Large Cap   
64      BBG00M1GKT62  BBG00M1GKT62  BBG00M1GKT62  EXCHOPT         Small Cap   
65      BBG00M1GKXB7  BBG00M1GKXB7  BBG00M1GKXB7  EXCHOPT         Small Cap   
66      BBG00M1GKW83  BBG00M1GKW83  BBG00M1GKW83  EXCHOPT         Small Cap   
67      BBG00NWPSPW7  BBG00NWPSPW7  BBG00NWPSPW7  EXCHOPT         Small Cap   
68      BBG00NWPSNP0  BBG00NWPSNP0  BBG00NWPSNP0  EXCHOPT         Small Cap   
69      BBG00NWPSPV8  BBG00NWPSPV8  BBG00NWPSPV8  EXCHOPT         Small Cap   
71      BBG00NC3M2H2  BBG00NC3M2H2  BBG00NC3M2H2  EXCHOPT         Small Cap   
75      BBG000BQQ2S6  BBG000BQQ2S6  BBG000BQQ2S6       EQ         Large Cap   
73      BBG00NYGND02  BBG00NYGND02  BBG00NYGND02  EXCHOPT         Small Cap   
72      BBG00MFH6JL6  BBG00MFH6JL6  BBG00MFH6JL6  EXCHOPT         Small Cap   
74      BBG00NYGNF43  BBG00NYGNF43  BBG00NYGNF43  EXCHOPT         Small Cap   

    SecurityId  DealTermsCash  DealTermsStock  DealValue DealClosingDate  \
70         NaN           59.0         15.7703    74.9338      2019-09-01   
64         NaN           59.0         15.7703    74.9338      2019-09-01   
65         NaN           59.0         15.7703    74.9338      2019-09-01   
66         NaN           59.0         15.7703    74.9338      2019-09-01   
67         NaN           59.0         15.7703    74.9338      2019-09-01   
68         NaN           59.0         15.7703    74.9338      2019-09-01   
69         NaN           59.0         15.7703    74.9338      2019-09-01   
71         NaN           59.0         15.7703    74.9338      2019-09-01   
75         NaN           59.0         15.7703    74.9338      2019-09-01   
73         NaN           59.0         15.7703    74.9338      2019-09-01   
72         NaN           59.0         15.7703    74.9338      2019-09-01   
74         NaN           59.0         15.7703    74.9338      2019-09-01   

    Equity_Risk_Factor  DV01  CR01  Adj_CR01 UltimateCountry   AlphaHedge  \
70            0.210456 